In [20]:
from IPython.display import display, HTML
#display(HTML("<style>.container { width:70% !important; }</style>"))

In [21]:
import pandas as pd
import numpy as np
import yfinance as yf
import scipy.optimize as sco
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

## Data download, formatting and stats

In [22]:
tickers = {
    "XOM": "XOM",
    "SHW": "SHW",
    "JPM": "JPM",
    "AEP": "AEP",
    "UNH": "UNH",
    "AMZN": "AMZN",
    "KO": "KO",
    "BA": "BA",
    "AMT": "AMT",
    "DD": "DD",
    "TSN": "TSN",
    "SLG": "SLG"
}

'''
tickers = {
    "CSPX.L": "S&P 500",
    "IWDA.L": "MSCI World",
    "CAC.PA": "CAC 40"
}
'''

nb_asset = len(tickers)

In [23]:
data = yf.download(tickers=list(tickers.keys()), period='15y', interval='1d')
# data = yf.download(tickers=list(tickers.keys()), start='2011-09-13', end='2022-01-09', interval='1d')

[*********************100%***********************]  12 of 12 completed


In [24]:
# Cleaning and formatting data
data = data['Adj Close']
data.rename(columns=tickers, inplace=True)
data = data.fillna(method='ffill')
data.dropna(inplace=True)

In [25]:
fig = go.Figure()
for key, ticker in tickers.items():
    fig.add_trace(go.Scatter(x=data.index, y=data[ticker], name='{}'.format(ticker)))
fig.update_layout(title_text='Stocks price evolution', height=650)
fig.show()

In [26]:
# Computing % change
data_change = pd.DataFrame()
for key, value in tickers.items():
    data_change['{}'.format(value)] = data['{}'.format(value)].pct_change(periods=1)
data_change.dropna(inplace=True)

In [27]:
# Computing annualized expected returns and covariance matrix
# mean_returns = (((data_change+1).prod()) ** (252.0 / (data_change.shape[0]))) - 1
mean_returns = data_change.mean() * 253
cov_matrix =  data_change.cov() * 253

In [28]:
fig = go.Figure(go.Bar(x=mean_returns, y=mean_returns.index, orientation='h', width=0.6, 
                       text=round(mean_returns * 100, 2)))
fig.update_traces(marker_color='#14C16B', marker_line_color='#08306B',
                  marker_line_width=1.5, opacity=0.7)
fig.update_layout(title_text='Geometric mean returns')
fig.show()

In [29]:
# Portfolio functions
def portfolio_return(weights, returns):
    return np.dot(weights, returns)


def portfolio_volatility(weights, covariance):
    return (np.dot(np.dot(weights, covariance), weights)) ** (1 / 2)


def sharpe_ratio(weights, returns, covariance):
    return -(portfolio_return(weights, returns) / portfolio_volatility(weights, covariance))

## Portfolio Optimization

In [30]:
# Defining the constraints
constraints = {"type": "eq", "fun": lambda x: np.sum(x) - 1.0}

# Defining the weight bounds
bounds = [(0.0, 1.0) for i in range(nb_asset)]

# Initial weights set as equally weighted portfolio
initial_weights = np.array([(1.0 / nb_asset) for i in range(nb_asset)])

#### Minimum variance portfolio

In [31]:
# Weights optimization for minimum variance portfolio
min_var_portfolio_results = sco.minimize(
    fun=portfolio_volatility,
    x0=initial_weights,
    args=cov_matrix,
    method='SLSQP',
    bounds=bounds,
    constraints=constraints
)

MVP_weights = list(min_var_portfolio_results.x)
print("Minimum variance portfolio weights: {}".format(np.round(MVP_weights, 2)))
MVP_return = portfolio_return(MVP_weights, mean_returns)
print("Minimum variance portfolio return: {}%".format(round(MVP_return * 100, 2)))
MVP_std = portfolio_volatility(MVP_weights, cov_matrix)
print("Minimum variance portfolio volatility: {}%".format(round(MVP_std * 100, 2)))
MVP_sr = sharpe_ratio(MVP_weights, mean_returns, cov_matrix)
print("Minimum variance portfolio Sharpe ratio: {}%".format(round(-MVP_sr * 100, 2)))

Minimum variance portfolio weights: [0.06 0.12 0.   0.28 0.   0.04 0.46 0.   0.   0.   0.04 0.  ]
Minimum variance portfolio return: 12.87%
Minimum variance portfolio volatility: 17.38%
Minimum variance portfolio Sharpe ratio: 74.06%


#### Maximum sharpe ratio portfolio

In [32]:
# Weights optimization for max sharpe ratio portfolio
max_sr_portfolio_results = sco.minimize(
    fun=sharpe_ratio,
    x0=initial_weights,
    args=(mean_returns, cov_matrix),
    method='SLSQP',
    bounds=bounds,
    constraints=constraints
)

MSR_weights = list(max_sr_portfolio_results.x)
print("Maximum sharpe portfolio weights: {}".format(np.round(MSR_weights, 2)))
MSR_return = portfolio_return(MSR_weights, mean_returns)
print("Maximum sharpe portfolio return: {}%".format(round(MSR_return * 100, 2)))
MSR_std = portfolio_volatility(MSR_weights, cov_matrix)
print("Maximum sharpe portfolio volatility: {}%".format(round(MSR_std * 100, 2)))
MSR_sr = sharpe_ratio(MSR_weights, mean_returns, cov_matrix)
print("Maximum sharpe portfolio Sharpe ratio: {}%".format(round(-MSR_sr * 100, 2)))

Maximum sharpe portfolio weights: [0.   0.36 0.   0.08 0.27 0.26 0.   0.   0.   0.   0.02 0.  ]
Maximum sharpe portfolio return: 23.65%
Maximum sharpe portfolio volatility: 22.97%
Maximum sharpe portfolio Sharpe ratio: 102.96%


#### Visualizing the portfolios weights

In [33]:
def round_list(numbers: list, dec: int):
    return [round(num, dec) for num in numbers]
fig = make_subplots(rows=1, cols=2, specs=[[{"type": "pie"}, {"type": "pie"}]])
fig.add_trace(go.Pie(labels=list(tickers.values()), values=round_list(MVP_weights, 6), title='Min var weights', showlegend=False,
                     hole=.6, hoverinfo="label+value", textposition='outside', textinfo='label+percent'), row=1, col=1)
fig.add_trace(go.Pie(labels=list(tickers.values()), values=round_list(MSR_weights, 6), title='Max sharpe weights', showlegend=False, 
                     hole=.6, hoverinfo="label+value", textposition='outside', textinfo='label+percent'), row=1, col=2)
fig.update_layout(title_text='Portfolios weights')
fig.show()

#### Random portfolios generation

In [34]:
nb_random_p = 10000

def random_weights_generator(nb_asset):
    random_weights = np.random.random(size=nb_asset)
    random_weights /= np.sum(random_weights)
    return random_weights

p_returns = []
p_stds = []
p_sr = []

for p in range(nb_random_p):
    rd_w = random_weights_generator(nb_asset)
    p_returns.append(portfolio_return(rd_w, mean_returns))
    p_stds.append(portfolio_volatility(rd_w, cov_matrix))
    p_sr.append(-sharpe_ratio(rd_w, mean_returns, cov_matrix))

#### Efficient frontier

In [35]:
# Defining the constraints
constraints = (
    {'type': 'eq', 'fun': lambda x: portfolio_return(x, mean_returns) - target_returns},
    {'type': 'eq', 'fun': lambda x: np.sum(x) - 1}
)

# Defining the weight bounds
bounds = [(0.0, 1.0) for i in range(nb_asset)]

# Initial weights set as equally weighted portfolio
initial_weights = np.array([(1.0 / nb_asset) for i in range(nb_asset)])

In [39]:
START = 0.12
END = 0.25

In [40]:
# Initialize an array of target returns
target_returns = np.linspace(
    start = START, 
    stop = END,
    num = 100
)

# Weights optimization for each target return
target_stds = []

for target_returns in target_returns:
    min_result_object = sco.minimize(
        fun=portfolio_volatility,
        x0=initial_weights,
        args=cov_matrix,
        method='SLSQP',
        bounds=bounds,
        constraints=constraints
    )
    target_stds.append(min_result_object['fun'])

target_returns = np.linspace(
    start = START, 
    stop = END,
    num = 100
)

#### Visualizing all portfolios

In [45]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=target_stds, y=target_returns, showlegend=False, line_color="#4C0099"))
fig.add_trace(go.Scatter(x=p_stds, y=p_returns, showlegend=False,  mode='markers', marker=dict(color=p_sr, colorscale='viridis', showscale=True)))
fig.add_trace(go.Scatter(x=[MSR_std], y=[MSR_return], showlegend=False, mode='markers', marker=dict(color='red', symbol='diamond', size=12), name='MSR portfolio'))
fig.add_trace(go.Scatter(x=[MVP_std], y=[MVP_return], showlegend=False, mode='markers', marker=dict(color='blue', symbol='diamond', size=12), name='MVP portfolio'))
fig.update_layout(height=700, title_text='Portfolios visualization')
fig.show()